# Análisis de Propagación de Spikes: Barrido 2D (K, rate_hz)

## Objetivo

Estudiar las probabilidades de activación de vecinos y el firing rate en función de:
- **K (acoplamiento recurrente)**: Factor de escalado de pesos sinápticos
- **rate_hz (input externo)**: Tasa de estímulo talámico

## Estrategia

1. **Barrido 2D**: Simular todas las combinaciones (K, rate_hz) → obtener (FR, P, σ)
2. **Matching por FR**: Para cada (K≠0, FR_target), encontrar K=0 con FR≈FR_target
3. **Contribución de red**: ΔP = P_coupled - P_baseline (mismo FR, diferente origen)
4. **Visualización**: Heatmaps, cortes 1D, análisis de ΔP(K, FR)

## Hipótesis

- FR ≈ a·rate_hz (relación casi lineal)
- K=0 define actividad espúrea (baseline)
- ΔP(K>0) captura la dinámica de red pura

---

## 1. Setup y Configuración

In [1]:
# from os import environ
# environ["OMP_NUM_THREADS"] = "1"
# environ["OPENBLAS_NUM_THREADS"] = "1"
# environ["MKL_NUM_THREADS"] = "1"
# environ["VECLIB_MAXIMUM_THREADS"] = "1"
# environ["NUMEXPR_NUM_THREADS"] = "1"

In [2]:
# =============================================================================
# IMPORTS
# =============================================================================
import os
import sys
from pathlib import Path

# Navegación al directorio raíz del proyecto
if Path.cwd().name == 'two_populations':
    os.chdir('../..')


import numpy as np
import matplotlib.pyplot as plt
from matplotlib import colors
import seaborn as sns
from brian2 import *
from datetime import datetime
from collections import defaultdict
import pickle
from tqdm.auto import tqdm
import pandas as pd
from scipy.interpolate import interp1d
from scipy.ndimage import gaussian_filter
from loguru import logger

# Imports del proyecto
from src.two_populations.model import IzhikevichNetwork
from src.two_populations.metrics import analyze_simulation_results
from src.two_populations.helpers.logger import setup_logger

# Configurar logger
logger = setup_logger(
    experiment_name="spike_propagation_2d",
    console_level="INFO",
    file_level="DEBUG",
    log_to_file=False
)

logger.info(f"Working directory: {Path.cwd()}")
logger.info(f"Timestamp: {datetime.now().strftime('%Y-%m-%d %H:%M:%S')}")

# Estilo de plots
plt.style.use('seaborn-v0_8-darkgrid')
sns.set_palette("husl")

/home/tonicoll/.conda/envs/neurophysics/lib/python3.11/site-packages/setuptools/_distutils/_msvccompiler.py:12: UserWarning: _get_vc_env is private; find an alternative (pypa/distutils#340)
  warnings.warn(
INFO     | __main__:<module>:40 - Working directory: /home/tonicoll/Projects/izhikevich
INFO     | __main__:<module>:41 - Timestamp: 2026-01-16 02:58:48


## 2. Parámetros del Barrido

In [3]:
# =============================================================================
# CONFIGURACIÓN DEL BARRIDO
# =============================================================================

# Tamaño de red
Ne = 800
Ni = 200

# Parámetros de simulación
SIM_CONFIG = {
    'dt_ms': 0.1,
    'T_ms': 4000,
    'warmup_ms': 500
}

# Parámetros fijos de red
NETWORK_PARAMS = {
    'Ne': Ne,
    'Ni': Ni,
    'noise_exc': 0.884,
    'noise_inh': 0.60,
    'p_intra': 0.1,
    'delay': 0.0,
    'stim_start_ms': None,
    'stim_duration_ms': SIM_CONFIG['T_ms'],
    'stim_base': 1.0,
    'stim_elevated': None
}

# Rango de parámetros a barrer
K_VALUES = np.arange(0,20,0.5)   # 17 valores
RATE_HZ_VALUES = np.arange(2,15,0.5)   # 11 valores
N_TRIALS = 5
N_PROCESSES = 29

# Parámetros del análisis de propagación
PROPAGATION_CONFIG = {
    'window_ms': 4.0,         # Ventana temporal para detectar respuestas
    'min_weight': 0.05,        # Peso mínimo para considerar conexión
    'min_spikes': 5,         # Mínimo de spikes para incluir neurona
}

# Seeds
FIXED_SEED = 100
VARIABLE_SEED = 200

# Directorio de salida
timestamp = datetime.now().strftime('%Y%m%d_%H%M%S')
OUTPUT_DIR = Path('results/spike_propagation_2d') / f'sweep_2d_{timestamp}'
OUTPUT_DIR.mkdir(parents=True, exist_ok=True)

logger.info(f"Barrido configurado:")
logger.info(f"  K values: {K_VALUES}")
logger.info(f"  rate_hz values: {RATE_HZ_VALUES}")
logger.info(f"  Total combinaciones: {len(K_VALUES) * len(RATE_HZ_VALUES)}")
logger.info(f"  Simulación: {SIM_CONFIG['T_ms']}ms @ dt={SIM_CONFIG['dt_ms']}ms")
logger.info(f"  Red: {Ne}E + {Ni}I, p_intra={NETWORK_PARAMS['p_intra']}")

INFO     | __main__:<module>:52 - Barrido configurado:
INFO     | __main__:<module>:53 -   K values: [ 0.   0.5  1.   1.5  2.   2.5  3.   3.5  4.   4.5  5.   5.5  6.   6.5
  7.   7.5  8.   8.5  9.   9.5 10.  10.5 11.  11.5 12.  12.5 13.  13.5
 14.  14.5 15.  15.5 16.  16.5 17.  17.5 18.  18.5 19.  19.5]
INFO     | __main__:<module>:54 -   rate_hz values: [ 2.   2.5  3.   3.5  4.   4.5  5.   5.5  6.   6.5  7.   7.5  8.   8.5
  9.   9.5 10.  10.5 11.  11.5 12.  12.5 13.  13.5 14.  14.5]
INFO     | __main__:<module>:55 -   Total combinaciones: 1040
INFO     | __main__:<module>:56 -   Simulación: 4000ms @ dt=0.1ms
INFO     | __main__:<module>:57 -   Red: 800E + 200I, p_intra=0.1


## 4. Función de Simulación Parametrizada

In [4]:
def run_single_simulation(k_factor, rate_hz, trial=0, verbose=False):
    """
    Ejecuta una simulación con parámetros (k_factor, rate_hz).
    
    Returns:
        dict con spike_times, spike_indices, synapses (i, j, w)
    """
    start_scope()
    
    # Crear red
    network = IzhikevichNetwork(
        dt_val=SIM_CONFIG['dt_ms'],
        T_total=SIM_CONFIG['T_ms'],
        fixed_seed=FIXED_SEED,
        variable_seed=VARIABLE_SEED + trial,
        trial=trial
    )
    
    # Parámetros de población
    params = {
        **NETWORK_PARAMS,
        'k_exc': k_factor,
        'k_inh': k_factor * 3.9,
        'rate_hz': rate_hz
    }
    
    # Crear población A
    pop_A = network.create_population2(name='A', **params)
    
    # IMPORTANTE: record_v_dt debe ser un número válido, no None
    # Setup monitors
    network.setup_monitors(['A'], record_v_dt=0.5, sample_fraction=0.25)
    
    # IMPORTANTE: Extraer conectividad ANTES de run_simulation
    # porque después de la simulación los objetos pueden estar en scope diferente
    syn = network.populations['A']['syn_intra']
    syn_i = np.array(syn.i[:])
    syn_j = np.array(syn.j[:])
    syn_w = np.array(syn.w[:])
    
    # Ejecutar simulación
    results = network.run_simulation()
    
    # Extraer spikes INMEDIATAMENTE
    spike_times = np.array(results['A']['spike_times'])
    spike_indices = np.array(results['A']['spike_indices'])
    

    # AÑADIR: Extraer voltajes
    v_mon = network.monitors['A']['voltage']
    v_times = np.array(v_mon.t / ms)
    v_values = np.array(v_mon.v / mV)
    v_neuron_ids = v_mon.record
        
    if verbose:
        logger.info(f"  Simulation completed: {len(spike_times)} spikes")
    
    # Retornar solo arrays numpy (pickleable)
    return {
        'k': k_factor,
        'rate_hz': rate_hz,
        'trial': trial,
        'spike_times': spike_times,
        'spike_indices': spike_indices,
        'v_times': v_times,
        'v_values': v_values,
        'v_neuron_ids': np.array(v_neuron_ids),
        'synapses': {
            'i': syn_i,
            'j': syn_j,
            'w': syn_w
        }
    }

logger.success("Simulation runner function defined")

SUCCESS  | __main__:<module>:75 - Simulation runner function defined


## 5. Barrido 2D: (K, rate_hz) → (FR, P, σ)

In [5]:
# =============================================================================
# PROPAGATION ANALYZER (OPTIMIZED)
# =============================================================================

class PropagationAnalyzer:
    """
    Analiza propagación forward E→X:
    Cuando neurona i dispara, ¿cuántos vecinos j responden en ventana temporal?
    
    Optimizaciones:
    - Búsqueda binaria (searchsorted) para encontrar respuestas en O(log N).
    - Vectorización donde es posible.
    """
    
    def __init__(self, window_ms=5.0, min_weight=0.05, min_spikes=5):
        self.window = window_ms
        self.min_weight = min_weight
        self.min_spikes = min_spikes
        
    def extract_connectivity(self, synapses_intra, Ne, target='all', verbose=False):
        """
        Extrae grafo de conectividad E→X desde sinapsis Brian2.
        """
        neighbors = defaultdict(list)
        weights = {}
        
        # Acceso rápido a arrays de Brian2
        pre_indices = np.array(synapses_intra.i)
        post_indices = np.array(synapses_intra.j)
        syn_weights = np.array(synapses_intra.w)
        
        # Filtro vectorizado: Solo E→X y peso > threshold
        # Asumimos que Ne separa excitatorias (0..Ne-1) de inhibitorias
        mask = (pre_indices < Ne) & (syn_weights >= self.min_weight)
        
        # 3. Filtro Postsináptico (Opcional)
        if target == 'exc':
            mask &= (post_indices < Ne)
        elif target == 'inh':
            mask &= (post_indices >= Ne)
        
        valid_pre = pre_indices[mask]
        valid_post = post_indices[mask]
        valid_w = syn_weights[mask]
        
        # Construcción del dict (esto es inevitablemente lento en Python pero se hace una vez)
        for pre, post, w in zip(valid_pre, valid_post, valid_w):
            neighbors[int(pre)].append(int(post))
            weights[(int(pre), int(post))] = float(w)
        
        if verbose:
            n_conns = len(valid_pre)
            if neighbors:
                degrees = [len(v) for v in neighbors.values()]
                logger.info(f"E→X connections: {n_conns} (avg degree: {np.mean(degrees):.1f})")
            else:
                logger.warning("No E→X connections found.")
        
        return dict(neighbors), weights
    
    def organize_spike_times(self, spike_times_arr, spike_indices_arr):
        """
        Organiza spikes por neurona.
        """
        spike_dict = defaultdict(list)
        # Zip es rápido, pero para millones de spikes pandas groupby es mejor.
        # Mantendremos zip por simplicidad si no son millones.
        for t, idx in zip(spike_times_arr, spike_indices_arr):
            spike_dict[int(idx)].append(float(t))
        
        # Convertir a numpy arrays ordenados (CRÍTICO para searchsorted)
        spike_dict = {k: np.sort(np.array(v)) for k, v in spike_dict.items()}
        return dict(spike_dict)
    
    def count_responses_vectorized(self, pre_spike_time, post_neuron_spikes):
        """
        Verifica si neurona post respondió en ventana [t, t+window).
        Usa búsqueda binaria: O(log N) vs O(N) de la versión anterior.
        """
        if len(post_neuron_spikes) == 0:
            return False
        
        # Buscamos dónde caería 'pre_spike_time'
        # searchsorted devuelve el índice donde se insertarían los valores manteniendo orden
        t_start = pre_spike_time
        t_end = pre_spike_time + self.window
        
        # Índice del primer spike >= t_start
        idx_start = np.searchsorted(post_neuron_spikes, t_start, side='left')
        
        # Si idx_start está fuera del array, no hay spikes posteriores
        if idx_start >= len(post_neuron_spikes):
            return False
            
        # Comprobamos si el spike encontrado está dentro de la ventana
        # Basta con mirar el spike en idx_start, porque es el primero >= t_start
        first_spike_after = post_neuron_spikes[idx_start]
        
        return first_spike_after < t_end
    
    def analyze(self, spike_dict, neighbors, T_total, warmup=0.0):
        """
        Análisis principal optimizado.
        """
        # Filtrar spikes por warmup (Vectorizado por neurona)
        spike_dict_filtered = {}
        total_spikes = 0
        n_neurons_active = 0
        
        for nid, times in spike_dict.items():
            valid_times = times[times >= warmup]
            if len(valid_times) > 0:
                spike_dict_filtered[nid] = valid_times
                total_spikes += len(valid_times)
                n_neurons_active += 1
                
        T_analysis = T_total - warmup
        if T_analysis <= 0: return {}
        
        ratios_per_spike = []
        activated_counts = []
        per_neuron_stats = {}
        
        total_spikes_analyzed = 0
        neurons_analyzed = 0
        
        # Bucle principal
        for pre_idx, post_neighbors in neighbors.items():
            if pre_idx not in spike_dict_filtered:
                continue
            
            pre_spikes = spike_dict_filtered[pre_idx]
            
            # Filtro de actividad mínima para estadística robusta
            if len(pre_spikes) < self.min_spikes:
                continue
            
            n_neighbors = len(post_neighbors)
            if n_neighbors == 0: continue
            
            neuron_ratios = []
            neuron_activated = []
            
            # Optimización: Pre-fetch de los spikes de los vecinos para no buscarlos en el dict cada vez
            neighbor_spikes_list = [
                spike_dict_filtered[post] 
                for post in post_neighbors 
                if post in spike_dict_filtered
            ]
            
            # Iterar sobre cada spike presináptico
            for spike_time in pre_spikes:
                n_activated = 0
                
                # Comprobar cada vecino (Ahora usando searchsorted)
                for post_spikes in neighbor_spikes_list:
                    if self.count_responses_vectorized(spike_time, post_spikes):
                        n_activated += 1
                
                ratio = n_activated / n_neighbors
                
                ratios_per_spike.append(ratio)
                activated_counts.append(n_activated)
                neuron_ratios.append(ratio)
                neuron_activated.append(n_activated)
                total_spikes_analyzed += 1
            
            # Estadísticas por neurona
            if neuron_ratios:
                per_neuron_stats[pre_idx] = {
                    'n_spikes': len(pre_spikes),
                    'n_neighbors': n_neighbors,
                    'mean_ratio': np.mean(neuron_ratios),
                    'mean_activated': np.mean(neuron_activated)
                }
                neurons_analyzed += 1
        
        # Cálculo final de métricas
        firing_rate = (total_spikes / max(1, n_neurons_active) / T_analysis) * 1000.0
        
        # Convertir a arrays para cálculos numpy seguros
        ratios_per_spike = np.array(ratios_per_spike) if ratios_per_spike else np.array([0.0])
        activated_counts = np.array(activated_counts) if activated_counts else np.array([0.0])
        
        results = {
            'P_transmission': float(np.mean(ratios_per_spike)),
            'P_transmission_std': float(np.std(ratios_per_spike)),
            'sigma': float(np.mean(activated_counts)),
            'sigma_std': float(np.std(activated_counts)),
            'firing_rate': float(firing_rate),
            # Guardamos distribuciones raw si se necesitan para histogramas
            'ratio_distribution': ratios_per_spike, 
            'activated_counts': activated_counts,
            'per_neuron': per_neuron_stats,
            'stats': {
                'n_neurons_analyzed': neurons_analyzed,
                'total_spikes_analyzed': total_spikes_analyzed,
                'total_spikes': total_spikes,
                'n_neurons_active': n_neurons_active,
                'T_analysis': T_analysis
            }
        }
        
        return results

logger.success("PropagationAnalyzer class defined (Optimized Version)")

SUCCESS  | __main__:<module>:206 - PropagationAnalyzer class defined (Optimized Version)


In [6]:
# =============================================================================
# HELPER: PROCESS SIMULATION RESULTS (E->All Configured)
# =============================================================================

from types import SimpleNamespace

# =============================================================================
# HELPER: PROCESS SIMULATION RESULTS (Clean & Lightweight)
# =============================================================================

def process_simulation_results(sim_data):
    """
    Procesa resultados de simulación para obtener métricas.
    - Elimina dependencia de 'loader'. Usa variables globales (Ne, SIM_CONFIG).
    - Elimina clase interna. Usa SimpleNamespace.
    """
    
    # 1. Configurar Analyzer (Usa config global)
    analyzer = PropagationAnalyzer(
        window_ms=PROPAGATION_CONFIG['window_ms'],
        min_weight=PROPAGATION_CONFIG['min_weight'],
        min_spikes=PROPAGATION_CONFIG['min_spikes']
    )
    
    # 2. Adaptador Rápido para Sinapsis (Dict -> Objeto)
    # Convierte el diccionario {'i': ..., 'w': ...} en un objeto donde se puede hacer obj.i
    syn_obj = SimpleNamespace(**sim_data['synapses'])
    
    # 3. Extraer conectividad
    # Usa la variable global 'Ne' directamente
    neighbors, weights = analyzer.extract_connectivity(
        synapses_intra=syn_obj, 
        Ne=Ne, 
        target='all', 
        verbose=False
    )
    
    # 4. Organizar spikes
    spike_dict = analyzer.organize_spike_times(
        sim_data['spike_times'],
        sim_data['spike_indices']
    )
    
    # 5. Analizar propagación
    # Usa la variable global 'SIM_CONFIG' directamente
    prop_results = analyzer.analyze(
        spike_dict=spike_dict,
        neighbors=neighbors,
        T_total=SIM_CONFIG['T_ms'],
        warmup=SIM_CONFIG['warmup_ms']
    )
    
    # 6. Empaquetar resultados
    # Nota: Asumimos estructura Smart Save donde params están anidados
    params = sim_data.get('params', sim_data) # Fallback por seguridad
    
    return {
        'k': params['k'],
        'rate_hz': params.get('rate', params.get('rate_hz')), # Compatible con 'rate' o 'rate_hz'
        'trial': params['trial'],
        'firing_rate': prop_results['firing_rate'],
        'P_transmission': prop_results['P_transmission'],
        'P_transmission_std': prop_results['P_transmission_std'],
        'sigma': prop_results['sigma'],
        'sigma_std': prop_results['sigma_std'],
        'n_neurons_analyzed': prop_results['stats']['n_neurons_analyzed'],
        'total_spikes': prop_results['stats']['total_spikes']
    }

logger.success("Helper function 'process_simulation_results' defined (Lightweight)")

# =============================================================================
# TASK RUNNER (GLOBAL FUNCTION FOR MULTIPROCESSING) - RAM SAFE VERSION
# =============================================================================
import uuid
import gzip
import uuid
import gzip

def run_single_task(args):
    """
    Smart Save: 
    - Trial 0: Guarda TODO (Voltajes alta resolución).
    - Trial > 0: Guarda SOLO Spikes (Ahorro del 99% de espacio).
    """
    k_val, rate_val, trial = args
    
    unique_id = uuid.uuid4().hex[:8]
    filename = f"raw_data_k{k_val:.2f}_r{rate_val:.1f}_t{trial}_{unique_id}.pkl.gz"
    filepath = OUTPUT_DIR / filename
    
    try:
        # 1. Simulación (Ahora con alta resolución)
        sim_data = run_single_simulation(
            k_factor=k_val,
            rate_hz=rate_val,
            trial=trial,
            verbose=False
        )
        
        # 2. Métricas
        metrics = process_simulation_results(sim_data)
        
        # 3. Lógica SMART SAVE
        include_voltage = (trial == 0)
        
        # Payload base (siempre spikes)
        raw_payload = {
            'spike_times': sim_data['spike_times'],      
            'spike_indices': sim_data['spike_indices'],  
            'params': {'k': k_val, 'rate': rate_val, 'trial': trial},
            'has_voltage': include_voltage 
        }
    
        
        if include_voltage:
            # Solo para Trial 0 procesamos la matriz pesada
            exc_mask = sim_data['v_neuron_ids'] < Ne
            
            # Casting a float32 para ahorrar 50% extra en el Trial 0
            v_exc_32 = sim_data['v_values'][exc_mask, :].astype(np.float32)
            v_times_32 = sim_data['v_times'].astype(np.float32)
            
            raw_payload['v_times'] = v_times_32
            raw_payload['v_exc'] = v_exc_32
            raw_payload['v_neuron_ids_exc'] = sim_data['v_neuron_ids'][exc_mask]
            raw_payload['N_exc_sampled'] = int(np.sum(exc_mask))
            raw_payload['synapses'] = sim_data['synapses']
        
        # 4. Guardar comprimido
        with gzip.open(filepath, 'wb') as f:
            pickle.dump(raw_payload, f)
            
        # Limpieza agresiva de memoria
        del sim_data, raw_payload
        if include_voltage:
            del v_exc_32, v_times_32
        
        return {
            **metrics,
            'raw_data_file': str(filepath),
            'status': 'success'
        }

    except Exception as e:
        logger.error(f"Error at K={k_val}, rate={rate_val}, trial={trial}: {str(e)}")
        return {
            'k': k_val, 'rate_hz': rate_val, 'trial': trial,
            'firing_rate': np.nan, 'P_transmission': np.nan,
            'P_transmission_std': np.nan, 'sigma': np.nan,
            'sigma_std': np.nan, 'n_neurons_analyzed': 0,
            'total_spikes': 0, 'raw_data_file': None,
            'status': 'failed', 'error_msg': str(e)
        }

logger.success("Helper function 'run_single_task' defined (RAM-Safe Mode)")

# =============================================================================
# 2D SWEEP WITH MULTIPROCESSING
# =============================================================================

def run_2d_sweep(K_values, rate_hz_values, n_trials=1, n_processes=None, save_results=True):
    """
    Ejecuta barrido 2D completo con múltiples trials en paralelo.
    Ahora guarda métricas + datos raw para análisis posterior.
    """
    import multiprocessing as mp
    
    # Generar lista de tareas (k, rate_hz, trial)
    tasks = []
    for k_val in K_values:
        for rate_val in rate_hz_values:
            for trial in range(n_trials):
                tasks.append((k_val, rate_val, trial))
    
    total_sims = len(tasks)
    
    logger.info(f"Starting 2D sweep: {total_sims} simulations")
    logger.info(f"K: {K_values}")
    logger.info(f"rate_hz: {rate_hz_values}")
    logger.info(f"n_trials: {n_trials}")
    
    if n_processes is None:
        n_processes = min(N_PROCESSES, total_sims)
    
    logger.info(f"Using {n_processes} parallel processes")
    
    # Ejecutar en paralelo con progress bar
    if n_processes > 1:
        with mp.Pool(processes=n_processes) as pool:
            results_list = list(tqdm(
                pool.imap(run_single_task, tasks),
                total=total_sims,
                desc="2D Sweep (parallel)"
            ))
    else:
        # Modo secuencial (útil para debugging)
        results_list = []
        for task in tqdm(tasks, desc="2D Sweep (sequential)"):
            results_list.append(run_single_task(task))
    
    # Separar métricas de raw_data para DataFrame
    metrics_list = []
    for result in results_list:
        if result is not None:
            # Extraer solo métricas para DataFrame
            metrics = {k: v for k, v in result.items() if k != 'raw_data'}
            metrics_list.append(metrics)
    
    # Convertir métricas a DataFrame
    df_results = pd.DataFrame(metrics_list)
    
    # Guardar resultados (métricas + raw_data completo)
    if save_results:
        output_file = OUTPUT_DIR / 'results.pkl'
        with open(output_file, 'wb') as f:
            pickle.dump({
                'df_results': df_results,
                'raw_data_files': [r['raw_data_file'] for r in results_list if r],  # Lista completa con raw_data
                'K_values': K_values,
                'rate_hz_values': rate_hz_values,
                'n_trials': n_trials,
                'config': {
                    'SIM_CONFIG': SIM_CONFIG,
                    'NETWORK_PARAMS': NETWORK_PARAMS,
                    'PROPAGATION_CONFIG': PROPAGATION_CONFIG
                }
            }, f)
        logger.success(f"Results saved to {output_file}")
    
    logger.success(f"2D sweep completed: {len(df_results)} simulations")
    
    return df_results

logger.success("2D sweep function defined")

SUCCESS  | __main__:<module>:70 - Helper function 'process_simulation_results' defined (Lightweight)
SUCCESS  | __main__:<module>:156 - Helper function 'run_single_task' defined (RAM-Safe Mode)
SUCCESS  | __main__:<module>:235 - 2D sweep function defined


In [7]:
# import os
# import sys
# import pickle
# import numpy as np
# import gzip
# from brian2 import *

# # --- IMPORTA TU CONFIGURACIÓN Y FUNCIÓN AQUÍ ---
# # (Asegúrate de que run_single_simulation y las constantes estén definidas arriba)

# def benchmark_storage():
#     print(f"--- INICIANDO BENCHMARK DE ALMACENAMIENTO ---")
#     print(f"Configuración: T={SIM_CONFIG['T_ms']}ms, dt={SIM_CONFIG['dt_ms']}ms")
#     print(f"Grabando voltajes de {int(Ne * 0.25)} neuronas con dt_record=0.1ms")
    
#     # 1. Ejecutar UNA sola simulación representativa
#     print("\nEjecutando simulación de prueba...")
#     data = run_single_simulation(k_factor=5.0, rate_hz=10.0, trial=0, verbose=True)
    
#     # 2. Prueba de guardado: Pickle Normal vs Pickle Comprimido
#     filename_raw = "test_size_raw.pkl"
#     filename_zip = "test_size_compressed.pkl.gz"
    
#     # Guardar Raw
#     with open(filename_raw, 'wb') as f:
#         pickle.dump(data, f)
        
#     # Guardar Comprimido (Gzip)
#     with gzip.open(filename_zip, 'wb') as f:
#         pickle.dump(data, f)
        
#     # 3. Medir tamaños
#     size_raw_mb = os.path.getsize(filename_raw) / (1024 * 1024)
#     size_zip_mb = os.path.getsize(filename_zip) / (1024 * 1024)
    
#     # 4. Proyección para el barrido completo
#     # K_VALUES (2) * RATE_HZ_VALUES (2) * N_TRIALS (2) = 8 en tu ejemplo actual
#     # Pero supongamos el barrido REAL que comentaste (17 K * 11 Rates * 5 Trials = 935 sims)
#     n_sims_real = 17 * 11 * 2 
    
#     total_raw_gb = (size_raw_mb * n_sims_real) / 1024
#     total_zip_gb = (size_zip_mb * n_sims_real) / 1024
    
#     print(f"\n--- RESULTADOS ---")
#     print(f"Tamaño por simulación (RAW):        {size_raw_mb:.2f} MB")
#     print(f"Tamaño por simulación (GZIP):       {size_zip_mb:.2f} MB")
#     print(f"Ratio de compresión:                {size_raw_mb/size_zip_mb:.2f}x")
#     print("-" * 30)
#     print(f"Proyección para {n_sims_real} simulaciones (Barrido completo estimado):")
#     print(f"Espacio necesario (RAW):            {total_raw_gb:.2f} GB")
#     print(f"Espacio necesario (GZIP):           {total_zip_gb:.2f} GB")
    
#     # Limpieza
#     os.remove(filename_raw)
#     os.remove(filename_zip)

# if __name__ == "__main__":
#     benchmark_storage()

In [8]:
# =============================================================================
# EJECUTAR BARRIDO 2D
# =============================================================================

# NOTA: Este bloque tarda ~30-60 minutos dependiendo del hardware y n_trials
# Puedes comentar esta celda y cargar resultados previos en la siguiente sección

logger.info("Starting 2D sweep...")
logger.info(f"Total simulations: {len(K_VALUES) * len(RATE_HZ_VALUES) * N_TRIALS}")
logger.info(f"Estimated time: ~{len(K_VALUES) * len(RATE_HZ_VALUES) * N_TRIALS * 0.3:.1f} min")

df_sweep = run_2d_sweep(
    K_values=K_VALUES,
    rate_hz_values=RATE_HZ_VALUES,
    n_trials=N_TRIALS,
    n_processes=N_PROCESSES,
    save_results=True
)

# Mostrar resumen
print("\n" + "="*80)
print("SWEEP SUMMARY")
print("="*80)
print(df_sweep.describe())
print("\n" + "="*80)

# Resumen por trial
if N_TRIALS > 1:
    print("\n" + "="*80)
    print("TRIAL VARIABILITY")
    print("="*80)
    trial_stats = df_sweep.groupby('trial')[['firing_rate', 'P_transmission', 'sigma']].agg(['mean', 'std'])
    print(trial_stats)
    print("\n" + "="*80)

INFO     | __main__:<module>:8 - Starting 2D sweep...
INFO     | __main__:<module>:9 - Total simulations: 5200
INFO     | __main__:<module>:10 - Estimated time: ~1560.0 min
INFO     | __main__:run_2d_sweep:178 - Starting 2D sweep: 5200 simulations
INFO     | __main__:run_2d_sweep:179 - K: [ 0.   0.5  1.   1.5  2.   2.5  3.   3.5  4.   4.5  5.   5.5  6.   6.5
  7.   7.5  8.   8.5  9.   9.5 10.  10.5 11.  11.5 12.  12.5 13.  13.5
 14.  14.5 15.  15.5 16.  16.5 17.  17.5 18.  18.5 19.  19.5]
INFO     | __main__:run_2d_sweep:180 - rate_hz: [ 2.   2.5  3.   3.5  4.   4.5  5.   5.5  6.   6.5  7.   7.5  8.   8.5
  9.   9.5 10.  10.5 11.  11.5 12.  12.5 13.  13.5 14.  14.5]
INFO     | __main__:run_2d_sweep:181 - n_trials: 5
INFO     | __main__:run_2d_sweep:186 - Using 29 parallel processes
SUCCESS  | src.two_populations.model:__init__:45 - Network initialized with seeds: {'trial': 1, 'fixed_seed_A': 99, 'fixed_seed_B': 101, 'fixed_seed_common': 100, 'variable_common_current': 204, 'variable_A_

2D Sweep (parallel):   0%|          | 0/5200 [00:00<?, ?it/s]

SUCCESS  | src.two_populations.model:__init__:45 - Network initialized with seeds: {'trial': 2, 'fixed_seed_A': 99, 'fixed_seed_B': 101, 'fixed_seed_common': 100, 'variable_common_current': 208, 'variable_A_current': 208, 'variable_B_current': 211}
SUCCESS  | src.two_populations.model:__init__:45 - Network initialized with seeds: {'trial': 0, 'fixed_seed_A': 99, 'fixed_seed_B': 101, 'fixed_seed_common': 100, 'variable_common_current': 200, 'variable_A_current': 200, 'variable_B_current': 203}
SUCCESS  | src.two_populations.model:__init__:45 - Network initialized with seeds: {'trial': 3, 'fixed_seed_A': 99, 'fixed_seed_B': 101, 'fixed_seed_common': 100, 'variable_common_current': 212, 'variable_A_current': 212, 'variable_B_current': 215}
SUCCESS  | src.two_populations.model:__init__:45 - Network initialized with seeds: {'trial': 1, 'fixed_seed_A': 99, 'fixed_seed_B': 101, 'fixed_seed_common': 100, 'variable_common_current': 204, 'variable_A_current': 204, 'variable_B_current': 207}
SUCC


SWEEP SUMMARY
                 k      rate_hz       trial  firing_rate  P_transmission  \
count  5200.000000  5200.000000  5200.00000  5200.000000     5200.000000   
mean      9.750000     8.250000     2.00000    20.399742        0.205378   
std       5.772253     3.750361     1.41435    12.623240        0.124070   
min       0.000000     2.000000     0.00000     0.768014        0.000000   
25%       4.875000     5.000000     1.00000     9.441571        0.083720   
50%       9.750000     8.250000     2.00000    20.225143        0.249680   
75%      14.625000    11.500000     3.00000    31.329500        0.314236   
max      19.500000    14.500000     4.00000    46.085714        0.373318   

       P_transmission_std        sigma    sigma_std  n_neurons_analyzed  \
count         5200.000000  5200.000000  5200.000000         5200.000000   
mean             0.102625    20.379891    10.406509          675.965769   
std              0.055749    12.358526     5.697786          282.294280   


In [ ]:
# import glob
# import re

# def run_resume_sweep(resume_dir, k_values, rate_values, target_trials, n_processes):
#     """
#     Escanea el directorio, detecta lo que falta y completa el trabajo.
#     """
#     resume_dir = Path(resume_dir)
#     if not resume_dir.exists():
#         raise FileNotFoundError(f"No encuentro el directorio: {resume_dir}")
    
#     logger.info(f"--- MODO REANUDACIÓN ---")
#     logger.info(f"Directorio: {resume_dir}")
    
#     # 1. ESCANEAR LO QUE YA TENEMOS
#     # Patrón de archivo: raw_data_k{k}_r{r}_t{t}_{uuid}.pkl.gz
#     logger.info("Escaneando archivos existentes...")
#     existing_files = list(resume_dir.glob("raw_data_*.pkl.gz"))
    
#     completed_tasks = set()
#     # Regex para extraer k, r, t del nombre del archivo
#     # Ejemplo: raw_data_k0.00_r10.0_t0_0d4039b7.pkl.gz
#     pattern = re.compile(r"raw_data_k([\d\.]+)_r([\d\.]+)_t(\d+)_")
    
#     for f in existing_files:
#         match = pattern.search(f.name)
#         if match:
#             k = float(match.group(1))
#             r = float(match.group(2))
#             t = int(match.group(3))
#             # Usamos redondeo para evitar errores de float al comparar
#             completed_tasks.add((round(k, 2), round(r, 2), t))
            
#     logger.info(f"Encontradas {len(completed_tasks)} simulaciones ya terminadas.")
    
#     # 2. GENERAR LISTA DE TAREAS FALTANTES
#     tasks_to_run = []
    
#     for k in k_values:
#         for r in rate_values:
#             for t in range(target_trials):
#                 # Clave para comparar
#                 task_key = (round(k, 2), round(r, 2), t)
                
#                 if task_key not in completed_tasks:
#                     tasks_to_run.append((k, r, t))
    
#     # Actualizar la variable global OUTPUT_DIR para que run_single_task guarde ahí
#     global OUTPUT_DIR
#     OUTPUT_DIR = resume_dir
    
#     if not tasks_to_run:
#         logger.success("¡Todo el trabajo ya está hecho! No faltan tareas.")
#         return
        
#     # 3. EJECUTAR LO QUE FALTA (SHUFFLED)
#     import random
#     random.shuffle(tasks_to_run)
    
#     logger.info(f"Faltan {len(tasks_to_run)} simulaciones para completar el objetivo.")
#     logger.info(f"Lanzando {n_processes} procesos...")
    
#     import multiprocessing as mp
#     with mp.Pool(processes=n_processes) as pool:
#         # Ejecutamos solo las pendientes
#         new_results = list(tqdm(
#             pool.imap_unordered(run_single_task, tasks_to_run),
#             total=len(tasks_to_run),
#             desc="Resuming Sweep"
#         ))
        
#     # 4. RECONSTRUCCIÓN FINAL DEL ÍNDICE (Merge Old + New)
#     # Escaneamos el directorio ENTERO de nuevo para crear un results.pkl completo
#     rebuild_index(resume_dir)

# def rebuild_index(directory):
#     """Reconstruye el results.pkl leyendo todos los raw_data files del disco"""
#     logger.info("Reconstruyendo índice maestro (results.pkl)...")
    
#     all_files = list(directory.glob("raw_data_*.pkl.gz"))
#     metrics_list = []
#     raw_files_list = []
    
#     # Procesamos archivos para extraer metadatos sin cargar todo el pickle (usamos el nombre)
#     # O cargamos el pickle ligero si queremos métricas exactas. 
#     # Para ir rápido y seguro, cargamos cada pkl.gz, leemos las métricas y cerramos.
#     # Esto puede tardar 1-2 mins pero asegura consistencia total.
    
#     for f in tqdm(all_files, desc="Indexing files"):
#         try:
#             with gzip.open(f, 'rb') as file:
#                 data = pickle.load(file)
                
#                 # Reconstruir métricas básicas si no están explícitas fuera
#                 # (Asumimos que run_single_task devolvía métricas, pero aquí leemos el raw file)
#                 # EL RAW FILE guardado en disco tiene 'spike_times', etc.
#                 # NO TIENE LAS MÉTRICAS PRE-CALCULADAS (P_trans, sigma).
#                 # Esas se devolvían en el return de la función.
                
#                 # OPCIÓN A: Recalcular métricas (Lento pero seguro)
#                 # OPCIÓN B: Confiar en que los returns de run_single_task se guardaron.
                
#                 # Como estamos reanudando y mezclando, lo mejor es recalcular métricas ligeras
#                 # O simplemente guardar la ruta y dejar que el notebook de análisis trabaje.
                
#                 # Para simplificar AHORA MISMO:
#                 # Vamos a guardar en el DF solo lo básico: k, r, t, y la ruta.
#                 # El análisis pesado se hará en el notebook de análisis.
                
#                 params = data['params']
#                 metrics_list.append({
#                     'k': params['k'],
#                     'rate_hz': params['rate'],
#                     'trial': params['trial'],
#                     'raw_data_file': str(f.relative_to(Path.cwd())), # Ruta relativa segura
#                     # Si quieres, aquí podrías llamar a process_simulation_results(data)
#                     # para recuperar firing_rate, etc.
#                 })
                
#         except Exception as e:
#             logger.warning(f"Archivo corrupto o ilegible: {f} - {e}")

#     df = pd.DataFrame(metrics_list)
    
#     # Guardar el índice final
#     output_pkl = directory / 'results.pkl'
#     with open(output_pkl, 'wb') as f:
#         pickle.dump({
#             'df_results': df,
#             'config': {'NOTE': 'Reconstructed from disk scan'}
#         }, f)
        
#     logger.success(f"Índice reconstruido con {len(df)} entradas en {output_pkl}")

# logger.success("Funciones de reanudación definidas.")

# # =============================================================================
# # CONFIGURACIÓN DE REANUDACIÓN (RESUME MODE)
# # =============================================================================

# # 1. PON AQUÍ LA CARPETA QUE QUIERES COMPLETAR
# # Ejemplo: "results/spike_propagation_2d/sweep_2d_20260116_001143"
# RESUME_DIR = Path("results/spike_propagation_2d/sweep_2d_20260116_011223") 

# # 2. CONFIGURACIÓN OBJETIVO (LO MISMO QUE TENÍAS)
# # Asegúrate de que estos rangos son los mismos que usaste al lanzar el original
# K_VALUES = np.arange(0, 20.1, 0.5)      
# RATE_HZ_VALUES = np.arange(0, 15.1, 0.5) 

# # AQUÍ DECIDES:
# # Si pones 10, completará hasta llegar a 10 trials (tardará las ~6h restantes).
# # Si pones 5, completará solo hasta tener 5 (tardará mucho menos).
# TARGET_TRIALS = 5  # Recomendado: 5 para acabar hoy. Pon 10 si quieres el full set.

# N_PROCESSES = 24 

# # (El resto de params se asumen iguales, no afectan a la lógica de reanudación)

# # EJECUTAR REANUDACIÓN
# run_resume_sweep(
#     resume_dir=RESUME_DIR,
#     k_values=K_VALUES,
#     rate_values=RATE_HZ_VALUES,
#     target_trials=TARGET_TRIALS, # 5 o 10, tú decides
#     n_processes=N_PROCESSES
# )

In [8]:
# =============================================================================
# AUTOMATIC PLOTTING
# =============================================================================

def generate_summary_plots(df, output_dir):
    """Genera y guarda figuras resumen del barrido"""
    
    # Agregar por (K, rate_hz)
    df_mean = df.groupby(['k', 'rate_hz']).agg({
        'firing_rate': 'mean',
        'P_transmission': 'mean',
        'sigma': 'mean'
    }).reset_index()
    
    # Crear grids para heatmaps
    K_unique = np.sort(df_mean['k'].unique())
    rate_unique = np.sort(df_mean['rate_hz'].unique())
    
    FR_grid = df_mean.pivot(index='k', columns='rate_hz', values='firing_rate').values
    P_grid = df_mean.pivot(index='k', columns='rate_hz', values='P_transmission').values
    sigma_grid = df_mean.pivot(index='k', columns='rate_hz', values='sigma').values
    
    # 1. Heatmaps principales
    fig, axes = plt.subplots(1, 3, figsize=(18, 5))
    
    im1 = axes[0].imshow(FR_grid, aspect='auto', origin='lower', cmap='viridis')
    axes[0].set_title('Firing Rate (Hz)', fontsize=14)
    axes[0].set_xlabel('rate_hz (Hz)')
    axes[0].set_ylabel('K (coupling)')
    plt.colorbar(im1, ax=axes[0])
    
    im2 = axes[1].imshow(P_grid, aspect='auto', origin='lower', cmap='plasma')
    axes[1].set_title('P_transmission', fontsize=14)
    axes[1].set_xlabel('rate_hz (Hz)')
    plt.colorbar(im2, ax=axes[1])
    
    im3 = axes[2].imshow(sigma_grid, aspect='auto', origin='lower', cmap='coolwarm')
    axes[2].set_title('σ (branching ratio)', fontsize=14)
    axes[2].set_xlabel('rate_hz (Hz)')
    plt.colorbar(im3, ax=axes[2])
    
    plt.tight_layout()
    plt.savefig(output_dir / 'heatmaps.png', dpi=300, bbox_inches='tight')
    plt.close()
    
    # 2. Curvas 1D: P vs K
    fig, axes = plt.subplots(1, 2, figsize=(14, 5))
    
    for rate in [4, 8, 12, 20]:
        mask = df_mean['rate_hz'] == rate
        axes[0].plot(df_mean[mask]['k'], df_mean[mask]['P_transmission'], 
                     'o-', label=f'rate={rate}Hz', markersize=6)
    
    axes[0].set_xlabel('K (coupling)', fontsize=12)
    axes[0].set_ylabel('P_transmission', fontsize=12)
    axes[0].legend()
    axes[0].grid(True, alpha=0.3)
    
    # σ vs K
    for rate in [4, 8, 12, 20]:
        mask = df_mean['rate_hz'] == rate
        axes[1].plot(df_mean[mask]['k'], df_mean[mask]['sigma'], 
                     'o-', label=f'rate={rate}Hz', markersize=6)
    
    axes[1].set_xlabel('K (coupling)', fontsize=12)
    axes[1].set_ylabel('σ (branching ratio)', fontsize=12)
    axes[1].legend()
    axes[1].grid(True, alpha=0.3)
    
    plt.tight_layout()
    plt.savefig(output_dir / 'curves_vs_K.png', dpi=300, bbox_inches='tight')
    plt.close()
    
    logger.success(f"Figures saved to {output_dir}")

# Generar plots automáticamente
generate_summary_plots(df_sweep, OUTPUT_DIR)

# Mostrar resumen
print("\n" + "="*80)
print("SWEEP SUMMARY")
print("="*80)
print(df_sweep.describe())
print("\n" + "="*80)

# Resumen por trial
if N_TRIALS > 1:
    print("\n" + "="*80)
    print("TRIAL VARIABILITY")
    print("="*80)
    trial_stats = df_sweep.groupby('trial')[['firing_rate', 'P_transmission', 'sigma']].agg(['mean', 'std'])
    print(trial_stats)
    print("\n" + "="*80)


SUCCESS  | __main__:generate_summary_plots:74 - Figures saved to results/spike_propagation_2d/sweep_2d_20260115_235126



SWEEP SUMMARY
               k    rate_hz      trial  firing_rate  P_transmission  \
count  20.000000  20.000000  20.000000    20.000000       20.000000   
mean    5.000000  11.000000   2.000000    13.927274        0.057426   
std     5.129892   9.233805   1.450953    12.421672        0.102108   
min     0.000000   2.000000   0.000000     1.846154        0.000000   
25%     0.000000   2.000000   1.000000     2.249442        0.000000   
50%     5.000000  11.000000   2.000000    11.610029        0.000000   
75%    10.000000  20.000000   3.000000    22.875500        0.054588   
max    10.000000  20.000000   4.000000    30.710444        0.238839   

       P_transmission_std      sigma  sigma_std  n_neurons_analyzed  \
count           20.000000  20.000000  20.000000           20.000000   
mean             0.029854   5.699653   3.023366          200.000000   
std              0.053109  10.134481   5.378355          355.409327   
min              0.000000   0.000000   0.000000            0.

# Resumen de Resultados: Spike Propagation 2D Sweep

## 📊 Hallazgos Principales

### 1. **Baseline vs Coupled Networks**
- **K=0 (sin recurrencia)**: P=0, σ=0 → ninguna propagación detectada
- **K>0**: Propagación emerge inmediatamente
  - K=0.5: P≈0.022 (2.2%), σ≈1.6
  - K=10: P≈0.270 (27%), σ≈21.4
  - **Incremento total**: ~12× en P, ~13× en σ

### 2. **Transición de Régimen Dinámico**

| Régimen | K range | P | σ | Interpretación |
|---------|---------|---|---|----------------|
| **Débil** | 0.5-2.0 | <0.03 | <2.5 | Propagación fallida |
| **Crítico** | 2.5-5.0 | 0.03-0.11 | 2.7-8.7 | Balance E/I |
| **Fuerte** | 7.0-10.0 | >0.18 | >14.5 | Cascadas robustas |

### 3. **Saturación**
- **P_transmission**: Empieza a saturar en K≈7 (crecimiento <15% por step)
- **σ (cascade size)**: Continúa creciendo linealmente hasta K=10
- **Firing rate**: Aumenta de 6Hz → 18.5Hz (correlacionado con K)

### 4. **Reproducibilidad (CV inter-trial)**
- **Firing rate**: CV≈2% → **excelente reproducibilidad**
- **P_transmission**: 
  - K bajos (≤4): CV=15-30% → variabilidad moderada
  - K altos (≥7): CV=2-4% → **muy estable**
- **Conclusión**: 5 trials son suficientes

### 5. **Efecto del Input Rate**
- **Rate <5Hz**: Insuficiente para propagación (valores filtrados)
- **Rate ≥5Hz**: Propagación robusta
- ⚠️ **Sesgo detectado**: Análisis agregado por rate es misleading debido a muestreo desbalanceado
- **Corrección necesaria**: Estratificar por bins de K para interpretar rate effect

---

## 🎯 Conclusiones

1. **La conectividad recurrente (K) es el driver principal** de spike propagation
   - Transición continua de sub- a super-crítico
   - Sin discontinuidades abruptas → sistema robusto

2. **El sistema NO alcanza runaway dynamics** a pesar de σ≈21
   - Input externo actúa como "clamp"
   - Similar a cortex in vivo (vs criticality clásica)

3. **Valores biológicamente plausibles**:
   - P_max≈27% → balance E/I realista
   - σ_max≈21 → cascadas finitas, no explosión
   - FR≈6-18Hz → rango fisiológico

4. **Limitaciones experimentales**:
   - Rate <5Hz produce datos poco informativos (30-100% zeros)
   - Re-run futuro debería: rate_hz ∈ [5, 20]Hz, 3 trials suficientes

5. **Próximos pasos**:
   - ✅ Shuffle test → validar significancia estadística
   - ✅ Weight/rate dependence → mecanismos subyacentes
   - ✅ Per-neuron heterogeneity → distribuciones
   - ⚠️ Corregir rate effect con análisis estratificado

## 12. Conclusiones y Próximos Pasos

### Resultados esperados:

1. **FR ≈ a·rate_hz**: Verificar linealidad entre input externo y firing rate
2. **P(K, rate_hz)**: Probabilidad de transmisión aumenta con K
3. **ΔP > 0 para K>0**: La red contribuye positivamente a la propagación
4. **σ(K) → 1**: Transición hacia criticalidad con acoplamiento óptimo

### Análisis complementarios:

- [ ] Barrido con delays (τ ≠ 0)
- [ ] Análisis de distribuciones de ISI
- [ ] Separación E/I en la propagación
- [ ] Correlación con INT
- [ ] Análisis de criticalidad (avalanchas)

### Optimizaciones:

- [ ] Paralelizar simulaciones (múltiples trials)
- [ ] Reducir resolución temporal en análisis
- [ ] Guardar solo métricas (no raster completo)

---

**Análisis crítico:**

**P≈96% es anómalo** con window=5ms (tau_syn=1.5ms + integración ~3ms). Casi todos los spikes activan vecinos → régimen super-crítico.

**Hallazgos clave:**

1. **Shuffle test:** Significativo (z=80, p<0.001) pero diferencia pequeña:
   - σ_real=8.93 vs σ_shuffled=7.39 (solo 21% mayor)
   - σ_shuffled alto → mucha correlación espuria incluso sin causalidad

2. **Correlaciones débiles:**
   - weight→P: r=0.14 (peso irrelevante, P saturado)
   - FR→P: r=0.21 (tasa casi no importa)

3. **Window sweep revela propagación extendida:**
   - P satura en 20ms (correcto)
   - σ crece hasta 100ms: σ(100)/σ(5) = 6.5× 
   - Cascadas de >2º orden dominan

**Conclusión:** K=4.0 + rate=10Hz + window=5ms captura régimen explosivo con propagación multi-orden. Para propagación monosináptica estricta, usar K≤2.0 y window=3ms.


## **Conclusiones**

### **2D Sweep (K × rate)**
- **K effect dominante**: P: 0.04→0.28 (7×), σ: 2.9→22.4 (7.7×)
- **Transición de régimen**: Débil (K<2) → Crítico (K=2-5) → Fuerte (K>7)
- **Saturación suave**: Empieza en K≈7, sin runaway dynamics
- **Rate effect**: Secundario, con sesgo de muestreo en rates <5Hz

### **Validación Estadística (K=5, rate=10Hz)**
- ✅ **Shuffle test**: σ significativo (p<0.001, z=83) → propagación NO aleatoria
- ⚠️ **P≈1.0 anómalo**: Casi todos los spikes excitatorios activan vecino
  - Posible régimen super-crítico en K=5 + rate=10Hz
  - Requiere verificación en otras condiciones

### **Optimizaciones Implementadas**
- Searchsorted: 5-10× más rápido (20 min → 3-5 min)
- Filtro excitatorio: Solo E→* como emisoras (correcto biológicamente)
- Funciones corregidas: `analyze_spike_propagation`, `weight_dependence`, `rate_dependence`, `per_neuron_metrics`

### **Limitaciones Detectadas**
- Time_window=50ms: Válido para propagación directa, pierde cascadas >100ms
- Rate <5Hz: Insuficiente para propagación detectable (30-100% zeros)
- Variabilidad inter-trial: CV≈22% aceptable pero mejorable

---

## **Next Steps**

### **Inmediato**
1. **Completar análisis extendido** (items 3-6 pendientes):
   - Weight dependence: ¿correlación positiva?
   - Per-neuron heterogeneity: distribuciones
   - Window sweep: saturación temporal
   
2. **Investigar P≈1.0**: Verificar en K=[2,3,4,7,10] si es real o bug

### **Corto plazo**
3. **Aplicar análisis a múltiples condiciones**:
   - Shuffle test en K=[0.5, 2, 5, 10] × rate=[6,10,15]
   - Validar significancia en todo el espacio paramétrico
   
4. **Visualizaciones finales**:
   - Weight dependence scatter plots
   - Per-neuron distributions (success_rate, σ_neuron)
   - Window saturation curves

### **Si re-corremos**
5. **Parámetros optimizados**:
   - rate_hz ∈ [5,6,7,8,10,12,15,20] (eliminar <5Hz)
   - n_trials = 3 (suficiente dado CV≈22%)
   - Total: 12K × 8rates × 3trials = 288 sims (~40% reducción)

### **Análisis futuro**
6. **Extensiones científicas**:
   - Comparar con datos experimentales (si disponibles)
   - Calcular power-law exponents (avalanches)
   - Relacionar σ con timescales intrínsecos (INT)

**Prioridad**: Terminar items 3-6 del análisis actual antes de re-correr.